# Adversarial Perturbation

In [ ]:
%cd /content
!gdown --fuzzy https://drive.google.com/file/d/1gj4itFieGOEuH2QjQOSx6AN_vZodOseo/view
!unzip -q /content/LP_detection_11.zip
!rm /content/LP_detection_11.zip

/content
Downloading...
From (original): https://drive.google.com/uc?id=1gj4itFieGOEuH2QjQOSx6AN_vZodOseo
From (redirected): https://drive.google.com/uc?id=1gj4itFieGOEuH2QjQOSx6AN_vZodOseo&confirm=t&uuid=caf42594-caa5-41f3-b628-264b86d79b78
To: /content/LP_detection_11.zip
100% 50.1M/50.1M [00:00<00:00, 116MB/s]
replace LP_detection_11/images/train/cropngoaigiao3.jpg? [y]es, [n]o, [A]ll, [N]one, [r]ename: A


In [ ]:
!git clone https://github.com/chancholat/adversarial_perturbation.git
%cd /content/adversarial_perturbation

fatal: destination path 'adversarial_perturbation' already exists and is not an empty directory.
/content/adversarial_perturbation


In [ ]:
from IPython.display import display
from skimage import io
from PIL import Image
import numpy as np
import shutil
import torch
import math
import cv2
import os
import plotly.express as px

In [ ]:
def visualize(image, bboxes, lp, verbose=True):
  bboxes = [np.round(bbox).astype(np.int32).tolist() for bbox in bboxes]
  for i in range(len(bboxes)):
    cv2.rectangle(image, (bboxes[i][0], bboxes[i][1]), (bboxes[i][2], bboxes[i][3]), (0, 255, 0), 2)

  # write character in below the boxes
  if len(bboxes):
    cv2.putText(image, lp, (bboxes[0][0], bboxes[0][1] - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (36,255,12), 2)
  # convert to RGB
  image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

  if verbose:
    fig = px.imshow(image)
    # axis off
    fig.update_layout(xaxis=dict(visible=False), yaxis=dict(visible=False))
    fig.show()
  else:
    return image

In [ ]:
def inference(cv2_images, det_model, ocr_model):
  images = det_model.preprocess(cv2_images)
  det_predictions = detect_model.detect(images)

  bboxes = detect_model.get_bboxes(det_predictions)
  crop_images = ocr_model.preprocess(images, bboxes)
  rec_predictions = ocr_model.detect(crop_images)
  lps, _ = ocr_model.get_plates_and_bboxes(rec_predictions)
  return images, lps, bboxes

In [ ]:
def deid(batch, det_model, deid_fn):
  images = det_model.preprocess(cv2_images)
  det_predictions = detect_model.detect(images)
  bboxes = detect_model.get_bboxes(det_predictions)

  adv_imgs = deid_fn.forward_batch(images, bboxes)
  return adv_imgs

In [ ]:
def attack(batch, adv_images, attacker, victims):
  adv_imgs = attacker.attack(
      victims=victims,
      images=batch,
      deid_images=adv_images)
  return adv_imgs

In [ ]:
from _models.detection.YoLoDetect import YOLOv5Detector
from _models.OCR.YoloOCR import YoloLicensePlateOCR
from attack.attacker.full_attacker import FullAttacker
from attack.deid import Blur

In [ ]:
detect_model = YOLOv5Detector()
ocr_model = YoloLicensePlateOCR()
deid_fn = Blur(14)
attacker = FullAttacker(
    optim='rmsprop',
    max_iter=250,
    eps=12/255.0,
    eps1=0.022834776253708135,
    eps2=0.043090941003692 / 5.0
  )


YOLOv5 🚀 2025-2-8 Python-3.11.11 torch-2.5.1+cu124 CUDA:0 (Tesla T4, 15095MiB)

Fusing layers... 
Model summary: 290 layers, 20852934 parameters, 0 gradients, 47.9 GFLOPs
Adding AutoShape... 
YOLOv5 🚀 2025-2-8 Python-3.11.11 torch-2.5.1+cu124 CUDA:0 (Tesla T4, 15095MiB)

Fusing layers... 
Model summary: 290 layers, 20970123 parameters, 0 gradients, 48.2 GFLOPs
Adding AutoShape... 


### Inference

In [ ]:
BATCH_SIZE = 4
IMAGE_DIR = '/content/LP_detection_11/images/train/'
cv2_images = []
bid = 24
for image_path in list(os.listdir(IMAGE_DIR))[bid:bid+BATCH_SIZE]:
    image = cv2.imread(os.path.join(IMAGE_DIR, image_path))
    cv2_images.append(image)

norm_images, lps, bboxes = inference(cv2_images, detect_model, ocr_model)

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is d

In [ ]:
bid = 1
visualize(norm_images[bid].copy(), bboxes[bid], lps[bid])
print(lps)
print(bboxes)

['54T1-5417', 'unknow', '63YV1-0200', 'unknow']
[[[192, 343, 302, 424]], [], [[328, 224, 451, 332]], [[190, 467, 255, 501]]]


### De Identification

In [ ]:
deid_imgs = deid(cv2_images, detect_model, deid_fn)

deid_images, lps, bboxes = inference(deid_imgs, detect_model, ocr_model)
bid = 0
visualize(deid_images[bid], bboxes[bid], lps[bid])
print(lps)
print(bboxes)

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is d

['unknow', 'unknow', 'unknow', 'unknow']
[[[190, 340, 306, 426]], [], [[327, 223, 451, 334]], []]


### Attack

In [ ]:
adv_imgs = attacker.attack(
    victims={
        "detection": detect_model,
        "OCR": ocr_model
    },
    images=cv2_images,
    deid_images=deid_imgs
)

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is d

Number of iter:  45


In [ ]:
adv_imgs = detect_model.preprocess(adv_imgs)
det_predictions = detect_model.detect(adv_imgs)
bboxes = detect_model.get_bboxes(det_predictions)
rec_predictions = ocr_model.detect(adv_imgs)
lps, _ = ocr_model.get_plates_and_bboxes(rec_predictions)

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_perturbation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is d

In [ ]:
for bid in range(len(adv_imgs)):
  result = visualize(adv_imgs[bid], bboxes[bid], lps[bid], False)
  norm_image = cv2.cvtColor(norm_images[bid].copy(), cv2.COLOR_RGB2BGR)
  concat = np.concatenate([norm_image, result], axis=1)
  fig = px.imshow(concat)
  # axis off
  fig.update_xaxes(showticklabels=False)
  fig.update_yaxes(showticklabels=False)
  fig.show()

### REFACTORING GURU (not to run)

In [ ]:
# from IPython.display import display
# from skimage import io
# from PIL import Image
# import numpy as np
# import shutil
# import torch
# import math
# import cv2
# import os
# import plotly.express as px

# def read_bbox(labels, multiboxes = False):
#     with open(labels, 'r') as file:
#       if multiboxes:
#         bboxes = []
#         for line in file:
#           line = line.strip().split(' ')[1:]
#           bboxes.append([float(i) for i in line])
#         return bboxes
#       else:
#         first_line = file.readline().strip().split(' ')[1:]
#         bbox = [float(i) for i in first_line]
#         return bbox

# def get_bbox(image_path, w, h):
#   label_path = image_path.replace("images", "labels").replace("jpg", "txt")
#   bbox = read_bbox(label_path)
#   xmin = (int)((bbox[0] - bbox[2] / 2) * w)
#   xmax = (int)((bbox[0] + bbox[2] / 2) * w)
#   ymin = (int)((bbox[1] - bbox[3] / 2) * h)
#   ymax = (int)((bbox[1] + bbox[3] / 2) * h)

#   return xmin, ymin, xmax, ymax

# def prepare_bbox_for_blurring(bbox, w, h):
#   # return xmin, xmax, ymin, ymax
#   xmin = (int)((bbox[0] - bbox[2] / 2) * w)
#   xmax = (int)((bbox[0] + bbox[2] / 2) * w)
#   ymin = (int)((bbox[1] - bbox[3] / 2) * h)
#   ymax = (int)((bbox[1] + bbox[3] / 2) * h)

#   return xmin, xmax, ymin, ymax

# def crop_image_for_ocr(image_path):
#   label_path = image_path.replace("images", "labels").replace("jpg", "txt")
#   img = cv2.imread(image_path)
#   h, w, _ = img.shape
#   bbox = get_bbox(label_path, w, h)
#   xmin, ymin, xmax, ymax = bbox
#   return img[ymin:ymax, xmin:xmax], img, bbox

# def visualize_bbox(image, bbox):
#   fig = px.imshow(image)
#   fig.update_layout(width=600, height=500, margin=dict(l=10, r=10, b=10, t=10), xaxis_title='Original image with bounding box')
#   fig.add_shape(type='rect',x0=bbox[0], x1=bbox[2], y0=bbox[1], y1=bbox[3], xref='x', yref='y',line_color='cyan')
#   fig.show()


#### Prepare


In [ ]:
# # Function to get bounding box for each detected character
# import math

# # license plate type classification helper function
# def linear_equation(x1, y1, x2, y2):
#     b = y1 - (y2 - y1) * x1 / (x2 - x1)
#     a = (y1 - b) / x1
#     return a, b

# def check_point_linear(x, y, x1, y1, x2, y2):
#     a, b = linear_equation(x1, y1, x2, y2)
#     y_pred = a*x+b
#     # print("distence: ", y_pred - y)
#     return(math.isclose(y_pred, y, abs_tol = 3)), y_pred - y

# # detect character and number in license plate
# def read_plate_and_bboxes(yolo_license_plate, im):
#     LP_type = "1"
#     results = yolo_license_plate(im, size=640)
#     bb_list = results.pandas().xyxy[0].values.tolist()
#     # if len(bb_list) == 0 or len(bb_list) < 7 or len(bb_list) > 10:
#     if len(bb_list) == 0:
#         return "unknown", bb_list, 0
#     center_list = []
#     y_mean = 0
#     y_sum = 0
#     for bb in bb_list:
#         x_c = (bb[0]+bb[2])/2
#         y_c = (bb[1]+bb[3])/2
#         y_sum += y_c
#         center_list.append([x_c,y_c,bb[-1]])

#     # find 2 point to draw line
#     l_point = center_list[0]
#     r_point = center_list[0]
#     min_distance = 300
#     for cp in center_list:
#         if cp[0] < l_point[0]:
#             l_point = cp
#         if cp[0] > r_point[0]:
#             r_point = cp
#     for ct in center_list:
#         if l_point[0] != r_point[0]:
#           check, distance = check_point_linear(ct[0], ct[1], l_point[0], l_point[1], r_point[0], r_point[1])
#           if abs(distance) < abs(min_distance):
#             min_distance = abs(distance)

#             # if (check_point_linear(ct[0], ct[1], l_point[0], l_point[1], r_point[0], r_point[1]) == False):
#           if check:
#                 LP_type = "2"

#     y_mean = int(int(y_sum) / len(bb_list))
#     size = results.pandas().s

#     # 1 line plates and 2 line plates
#     line_1 = []
#     line_2 = []
#     license_plate = ""
#     # print("Lp_type:", LP_type)
#     if LP_type == "2":
#         for c in center_list:
#             if int(c[1]) > y_mean:
#                 line_2.append(c)
#             else:
#                 line_1.append(c)
#         for l1 in sorted(line_1, key = lambda x: x[0]):
#             license_plate += str(l1[2])
#         license_plate += "-"
#         for l2 in sorted(line_2, key = lambda x: x[0]):
#             license_plate += str(l2[2])
#     else:
#         for l in sorted(center_list, key = lambda x: x[0]):
#             license_plate += str(l[2])
#     return license_plate, bb_list, min_distance

In [ ]:
# # %cd /content/License-Plate-Recognition
# from IPython.display import display
# from skimage import io
# from PIL import Image
# import numpy as np
# import shutil
# import torch
# import math
# import cv2
# import os
# import function.utils_rotate as utils_rotate
# import plotly.express as px

In [ ]:
# # Download YOLOv5 model from Ultralytics
# !git clone https://github.com/ultralytics/yolov5.git

Cloning into 'yolov5'...
remote: Enumerating objects: 17265, done.
remote: Counting objects: 100% (92/92), done.
remote: Compressing objects: 100% (82/82), done.
remote: Total 17265 (delta 46), reused 10 (delta 10), pack-reused 17173 (from 5)
Receiving objects: 100% (17265/17265), 16.00 MiB | 21.23 MiB/s, done.
Resolving deltas: 100% (11791/11791), done.


In [ ]:
# %cd /content/License-Plate-Recognition
# yolo_LP_OCR = torch.hub.load('yolov5', 'custom', path='model/LP_ocr.pt', force_reload=True, source='local')

In [ ]:
# for param in yolo_LP_OCR.model.model.parameters():
#     param.requires_grad = False

In [ ]:
# image_path = "/content/LP_detection_11/images/train/xemay1030.jpg"
# ocr_img, image, bbox = crop_image_for_ocr(image_path)

# lp = ""
# list_read_plates = []
# list_read_char_bbox = []
# for cc in range(0,2):
#     for ct in range(0,2):
#         lp, bboxes, min_distance = read_plate_and_bboxes(yolo_LP_OCR, utils_rotate.deskew(ocr_img, cc, ct))
#         if lp != "unknown":
#             list_read_plates.append(lp)
#             list_read_char_bbox.append(bboxes)
#             flag = 1
#             break
#     if flag == 1:

#         break

# print(list_read_plates)
# print(list_read_char_bbox)
# visualize_bbox(image, bbox)

/content/License-Plate-Recognition/yolov5/models/common.py:894: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast(autocast):


['543-0018']
[[[17.755298614501953, 11.19989013671875, 26.736337661743164, 34.40961456298828, 0.8979786038398743, 4, '5'], [17.34193992614746, 39.50263595581055, 26.416440963745117, 61.952388763427734, 0.8873956203460693, 29, '0'], [58.49568176269531, 40.55978012084961, 67.85995483398438, 63.49698257446289, 0.8797189593315125, 7, '8'], [59.18422317504883, 12.903570175170898, 67.99813079833984, 35.90239715576172, 0.8746537566184998, 2, '3'], [30.728090286254883, 39.739959716796875, 40.457942962646484, 62.568599700927734, 0.8724366426467896, 29, '0'], [28.77073097229004, 12.951168060302734, 36.55413818359375, 34.78386688232422, 0.8549255728721619, 3, '4'], [44.706886291503906, 40.313743591308594, 52.433650970458984, 63.1510124206543, 0.803394079208374, 0, '1']]]


In [ ]:

# from yolov5.utils.augmentations import letterbox
# def preprocess(images):
#   preprocess_imgs = []

#   for img in images:
#     # Resizes and pads image to new_shape (640 for yolo) with stride-multiple constraints, returns resized image, ratio, padding.
#     pad_img, ratio, pad = letterbox(img, 640, auto=False, scaleup=True)

#     # pad_img = pad_img.transpose((2, 0, 1))[::-1]  # HWC to CHW, BGR to RGB
#     # pad_img = np.ascontiguousarray(pad_img)
#     preprocess_imgs.append(pad_img)

#   preprocess_imgs = np.stack(preprocess_imgs, axis=0)
#   # preprocess_imgs =  torch.from_numpy(preprocess_imgs)
#   return preprocess_imgs

# image_paths = [ "/content/LP_detection_11/images/train/xemay1030.jpg"]
# input = [crop_image_for_ocr(path) for path in image_paths]
# images = [i[0] for i in input]
# predictions = []
# yolo_LP_OCR.eval()
# list_read_plates = []
# images =  preprocess(images)
# print(images.shape)
# for img in images:
#   pred = yolo_LP_OCR(img, size=640)
#   boxes = pred.pandas().xyxy[0].values.tolist()
#   predictions.append(boxes)

# for pred in predictions:
#   print(pred)

(1, 640, 640, 3)


/content/License-Plate-Recognition/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.



[[131.02923583984375, 98.40005493164062, 198.7528076171875, 270.0362243652344, 0.8957139253616333, 4, '5'], [437.00372314453125, 115.94502258300781, 502.38616943359375, 283.924560546875, 0.8859183192253113, 2, '3'], [211.93482971191406, 110.96393585205078, 271.2134094238281, 273.1523742675781, 0.8814942836761475, 3, '4'], [224.95323181152344, 309.9425048828125, 297.18572998046875, 477.2855224609375, 0.8807771801948547, 29, '0'], [126.23373413085938, 307.6496276855469, 194.00619506835938, 471.0318298339844, 0.8790179491043091, 29, '0'], [429.4272155761719, 320.1829833984375, 498.6315002441406, 487.554931640625, 0.8720064163208008, 7, '8'], [327.6639099121094, 314.2901611328125, 384.9511413574219, 485.41912841796875, 0.8376758098602295, 0, '1']]


#### OCR

In [ ]:
# import torch.nn as nn

# class BaseOCR(nn.Module):
#     """
#     Base Detector abstract class
#     """
#     def __init__(self):
#         super().__init__()

#     def preprocess(self, images, bboxes):
#         """
#         Preprocess the input images before being passed into model
#         :params:
#             images: images in cv2 format.
#             bboxes: bounding boxes of license plate in the images, required in format [xmin, ymin, xmax, ymax ...]
#         :return: processed image after being cropped after bboxes and padded
#         """
#         raise NotImplementedError("This is an interface method")

#     def postprocess(self, adv_images):
#         """
#         Postprocess the adversarial image after being attacked.
#         Convert the adversarial image into cv2 format
#         :params:
#             adv_images: attacked images.
#         :return: cv2 image
#         """
#         raise NotImplementedError("This is an interface method")

#     def forward(self, adv_images, targets):
#         """
#         Forward the attacking image and targets to compute gradients
#         :params:
#             adv_images: adversarial images, also stores gradients.
#             targets: targets fit model and adversarial image.
#         :return: adversarial images
#         """
#         raise NotImplementedError("This is an interface method")

#     def detect(self, query_input):
#         """
#         Model inference on the processed input
#         :params:
#             query_input: processed input. The images have been cropped and padded
#         :return: model predictions
#         """
#         raise NotImplementedError("This is an interface method")

#     def make_targets(self, predictions, images):
#         """
#         Make the targets from the predictions of model
#         :params:
#             predictions: model prediction.
#             images: list of cv2 image.
#         :return: model targets
#         """
#         raise NotImplementedError("This is an interface method")

#     def get_plate_and_bboxes(self, predictions):
#         """
#         Extract the bounding box from model predictions
#         :params:
#             predictions: model prediction.

#         :return:
#           lp: license plate characters and
#           bboxes: bounding box of characters in the license plate. In (x1,y1,x2,y2) format
#         """
#         raise NotImplementedError("This is an interface method")

In [ ]:
# from yolov5.utils.augmentations import letterbox
# from yolov5.utils.general import xyxy2xywhn
# from yolov5.utils.loss import ComputeLoss
# import torch
# import torch.nn as nn

# def crop_image(image, bbox):
#   xmin, ymin, xmax, ymax = bbox
#   return image[ymin:ymax, xmin:xmax]

# def yoloLPOCR():
#   yolo_LP_OCR = torch.hub.load('yolov5', 'custom', path='model/LP_ocr.pt', force_reload=True, source='local')
#   for param in yolo_LP_OCR.model.model.parameters():
#     param.requires_grad = False
#   return yolo_LP_OCR

# class YoloLicensePlateOCR(BaseOCR):
#   def __init__(self):
#     super(YoloLicensePlateOCR, self).__init__()

#     self.model = yoloLPOCR()
#     self.model.eval()
#     self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#     self.model = self.model.to(self.device)
#     self.compute_loss = ComputeLoss(self.model.model.model)

#   def preprocess(self, images, bboxes):
#     preprocess_imgs = []

#     for img, bbox in zip(images, bboxes):
#       crop_img = crop_image(img, bbox)
#       # Resizes and pads image to new_shape (640 for yolo) with stride-multiple constraints, returns resized image, ratio, padding.
#       pad_img, ratio, pad = letterbox(crop_img, 640, auto=False, scaleup=True)

#       # pad_img = pad_img.transpose((2, 0, 1))[::-1]  # HWC to CHW, BGR to RGB
#       # pad_img = np.ascontiguousarray(pad_img)
#       preprocess_imgs.append(pad_img)

#     preprocess_imgs = np.stack(preprocess_imgs, axis=0)
#     # preprocess_imgs =  torch.from_numpy(preprocess_imgs)
#     return preprocess_imgs

#   def postprocess(self, adv_images):
#     adv_images = adv_images.detach().cpu().numpy().transpose(1,2,0) * 255.0
#     adv_images = cv2.cvtColor(adv_images, cv2.COLOR_RGB2BGR)
#     return adv_images

#   def forward(self, adv_images, targets):
#     self.model.model.model.train()

#     if len(adv_images.shape) == 3:
#       adv_images = adv_images.unsqueeze(0)

#     adv_images = adv_images.to(self.device)
#     targets = targets.to(self.device)

#     predictions = self.model.model.model(adv_images)
#     loss, loss_items = self.compute_loss(predictions, targets)

#     self.model.model.model.eval()
#     return loss

#   def detect(self, images):
#     self.model.eval()
#     predictions = []

#     if len(images.shape) == 3:
#       images = images.unsqueeze(0)

#     for img in images:
#       pred = self.model(img, size=640)
#       pred = pred.pandas().xyxy[0].values.tolist()
#       predictions.append(pred)

#     return predictions

#   def make_targets(self, predictions, images):
#     targets = []
#     for i, (pred, image) in  enumerate(zip(predictions, images)):
#       h, w, _ = image.shape

#       # extract class number, xmin, ymin, xmax, ymax
#       pred = np.array([[item[5], item[0], item[1], item[2], item[3]] for item in pred])

#       if len(pred) == 0:
#         pred = np.zeros((0, 6))

#       nl = len(pred)
#       target = torch.zeros((nl, 6))
#       # convert xyxy to xc, yc, wh
#       pred[:, 1:5] = xyxy2xywhn(pred[:, 1:5], w=w, h=h, clip=True, eps=1e-3)
#       target[:, 1:] = torch.from_numpy(pred)

#       # add image index for build target
#       target[:, 0] = i
#       targets.append(target)

#     return torch.cat(targets)


#   def get_plates_and_bboxes(self, predictions):
#     lps = []
#     bboxes = []
#     for pred in predictions:
#       if len(pred) == 0:
#           return "unknown", pred
#       center_list = []
#       y_mean = 0
#       y_sum = 0
#       for bb in pred:
#           x_c = (bb[0]+bb[2])/2
#           y_c = (bb[1]+bb[3])/2
#           y_sum += y_c

#           # x center, y center and the character
#           center_list.append([x_c,y_c,bb[-1]])

#       # find 2 point to draw line
#       l_point = center_list[0]
#       r_point = center_list[0]
#       min_distance = 300
#       for cp in center_list:
#           if cp[0] < l_point[0]:
#               l_point = cp
#           if cp[0] > r_point[0]:
#               r_point = cp
#       for ct in center_list:
#           if l_point[0] != r_point[0]:
#             check, distance = check_point_linear(ct[0], ct[1], l_point[0], l_point[1], r_point[0], r_point[1])
#             if abs(distance) < abs(min_distance):
#               min_distance = abs(distance)

#               # if (check_point_linear(ct[0], ct[1], l_point[0], l_point[1], r_point[0], r_point[1]) == False):
#             if check:
#                   LP_type = "2"

#       y_mean = int(int(y_sum) / len(pred))

#       # 1 line plates and 2 line plates
#       line_1 = []
#       line_2 = []
#       license_plate = ""
#       # print("Lp_type:", LP_type)
#       if LP_type == "2":
#           for c in center_list:
#               if int(c[1]) > y_mean:
#                   line_2.append(c)
#               else:
#                   line_1.append(c)
#           for l1 in sorted(line_1, key = lambda x: x[0]):
#               license_plate += str(l1[2])
#           license_plate += "-"
#           for l2 in sorted(line_2, key = lambda x: x[0]):
#               license_plate += str(l2[2])
#       else:
#           for l in sorted(center_list, key = lambda x: x[0]):
#               license_plate += str(l[2])

#       lps.append(license_plate)
#       bboxes.append(pred)
#     return lps, bboxes


#### Attack


##### Opitmizer

In [ ]:
# """
# Copied from https://github.com/honguyenhaituan/PrivacyPreservingFaceRecognition/blob/16afc9df67afafe626a42ae7a5173547e9adae21/attacks/optim.py#L80
# author: honguyenhaituan
# """

# import torch
# from torch.optim import Adadelta, Adagrad, Adam, AdamW, Adamax, ASGD, RMSprop, Rprop, SGD
# from torch.optim.optimizer import Optimizer

# class I_FGSM:
#     def __init__(self, params, epsilon=8/255., alpha=1/255., min_value=0, max_value=1):
#         self.params = params
#         self.epsilon = epsilon
#         self.alpha = alpha
#         self.min_value = min_value
#         self.max_value = max_value
#         self.updated_params = []
#         for param in self.params:
#             self.updated_params.append(torch.zeros_like(param))

#     @torch.no_grad()
#     def _cal_update(self, idx):
#         return -self.alpha * torch.sign(self.params[idx].grad)

#     @torch.no_grad()
#     def step(self):
#         for idx, (param, updated_param) in enumerate(zip(self.params, self.updated_params)):
#             if param is None:
#                 continue

#             n_update = torch.clamp(updated_param + self._cal_update(idx), -self.epsilon, self.epsilon)
#             update = n_update - updated_param
#             n_param = torch.clamp(param + update, self.min_value, self.max_value)
#             update = n_param - param

#             param += update
#             updated_param += update

#     def zero_grad(self):
#         for param in self.params:
#             if param.grad is not None:
#                 param.grad.zero_()

# class MI_FGSM(I_FGSM):
#     def __init__(self, params, epsilon=8/255., momemtum=0, **kwargs):
#         super(MI_FGSM, self).__init__(params, epsilon, **kwargs)
#         self.momentum = momemtum
#         self.o_grad = []
#         for param in self.params:
#             self.o_grad.append(torch.zeros_like(param))

#     @torch.no_grad()
#     def _cal_update(self, idx):
#         grad = self.o_grad[idx] * self.momentum + self.params[idx].grad / torch.sum(torch.abs(self.params[idx].grad))
#         return -self.alpha * torch.sign(grad)

#     def zero_grad(self):
#         for o_grad, param in zip(self.o_grad, self.params):
#             if param.grad is not None:
#                 o_grad = o_grad * self.momentum + param.grad / torch.sum(torch.abs(param.grad))
#         super().zero_grad()



# class WrapOptim:
#     @torch.no_grad()
#     def __init__(self, params, epsilon, optimizer:Optimizer, min_value=0, max_value=1):
#         self.optim = optimizer
#         self.params = params
#         self.epsilon = epsilon
#         self.min_value = min_value
#         self.max_value = max_value
#         self.params_init = []
#         for param in params:
#             self.params_init.append(param.clone())

#     @torch.no_grad()
#     def step(self):
#         self.optim.step()
#         for param, param_init in zip(self.params, self.params_init):
#             total_update = param - param_init
#             update = torch.clamp(total_update, -self.epsilon, self.epsilon)

#             param += update - total_update
#             param.clamp_(self.min_value, self.max_value)

#     def zero_grad(self):
#         self.optim.zero_grad()

# def get_optim(name, params, epsilon, **kwargs) -> I_FGSM:
#     if name == 'i-fgsm':
#         return I_FGSM(params, epsilon, **kwargs)
#     if name == 'mi-fgsm':
#         return MI_FGSM(params, epsilon, **kwargs)

#     optimizer = None
#     if name == 'adadelta':
#         optimizer = Adadelta(params)
#     if name == 'adagrad':
#         optimizer = Adagrad(params)
#     if name == 'adam':
#         optimizer = Adam(params)
#     if name == 'adamw':
#         optimizer = AdamW(params)
#     if name == 'adamax':
#         optimizer = Adamax(params)
#     if name == 'asgd':
#         optimizer = ASGD(params)
#     if name == 'rmsprop':
#         optimizer = RMSprop(params, lr=0.004)
#     if name == 'rprop':
#         optimizer = Rprop(params)
#     if name == 'sgd':
#         optimizer = SGD(params)

#     if optimizer:
#         return WrapOptim(params, epsilon, optimizer, **kwargs)

#     return None


##### DeID

In [ ]:
# import numpy as np
# import cv2

# # Tested the original code.

# class DeID:
#     """
#     Base class for deid function
#     """
#     def __init__(self) -> None:
#         pass

#     def forward_batch(self, images, bboxes):
#         """
#         Forward batch of images
#         """
#         deid_images = []
#         for (image, bbox) in zip(images, bboxes):
#           if len(bbox):
#             deid_images.append(self(image, bbox[0])) # assume there only one bbox per image
#           else:
#             deid_images.append(image)
#         return deid_images

# class Pixelate(DeID):
#     """
#     Pixelate face in the image
#     :params:
#         blocks: number of pixelated blocks
#     """
#     def __init__(self, blocks=3) -> None:
#         super().__init__()
#         self.blocks = blocks

#     def __call__(self, image, bbox):
#         """
#         :params:
#             image: cv2 image
#             bbox: bounding box of face. In (x1,y1,x2,y2) format
#         """
#         x1,y1,x2,y2 = bbox
#         crop = image[y1:y2, x1:x2, :]

#         # divide the input image into NxN blocks
#         (h, w) = crop.shape[:2]
#         xSteps = np.linspace(0, w, self.blocks + 1, dtype="int")
#         ySteps = np.linspace(0, h, self.blocks + 1, dtype="int")
#         # loop over the blocks in both the x and y direction
#         for i in range(1, len(ySteps)):
#             for j in range(1, len(xSteps)):
#                 # compute the starting and ending (x, y)-coordinates
#                 # for the current block
#                 startX = xSteps[j - 1]
#                 startY = ySteps[i - 1]
#                 endX = xSteps[j]
#                 endY = ySteps[i]
#                 # extract the ROI using NumPy array slicing, compute the
#                 # mean of the ROI, and then draw a rectangle with the
#                 # mean RGB values over the ROI in the original image
#                 roi = crop[startY:endY, startX:endX]

#                 (B, G, R) = [int(x) for x in cv2.mean(roi)[:3]]
#                 cv2.rectangle(crop, (startX, startY), (endX, endY),
#                 (B, G, R), -1)

#         image[y1:y2, x1:x2, :] = crop.copy()

#         # return the pixelated blurred image
#         return image

# class Blur(DeID):
#     """
#     Gaussian Blur face in the image
#     :params:
#         blocks: Gaussian filter size
#     """
#     def __init__(self, kernel_size=3) -> None:
#         super().__init__()
#         self.kernel_size = (kernel_size, kernel_size)

#     def __call__(self, image, bbox):
#         """
#         :params:
#             image: cv2 image
#             bbox: bounding box of face. In (x1,y1,x2,y2) format
#         """
#         x1,y1,x2,y2 = bbox
#         crop = image[y1:y2, x1:x2, :]
#         crop = cv2.blur(crop, self.kernel_size)
#         image[y1:y2, x1:x2, :] = crop.copy()

#         # return the blurred image
#         return image

In [ ]:
# def deid(batch, det_model, deid_fn):
#   images = det_model.preprocess(cv2_images)
#   det_predictions = detect_model.detect(images)
#   bboxes = detect_model.get_bboxes(det_predictions)

#   adv_imgs = deid_fn.forward_batch(images, bboxes)
#   return adv_imgs

##### Atacker

In [ ]:
# import torch
# from torchvision.transforms import functional as TFF


# def generate_tensors(query):
#     """
#     Generate tensors to allow computing gradients
#     :params:
#         query: list of cv2 image
#     :return: torch tensors of images
#     """
#     if len(query.shape)==3:
#         query = [query]

#     if isinstance(query[0], torch.Tensor):
#         torch_images = query
#     else:
#         torch_images = [
#             TFF.to_tensor(i) if query.shape[-1] == 3 else torch.from_numpy(i) for i in query]

#     return torch.stack(torch_images, dim=0).contiguous()

# class Attacker:
#     """
#     Abstract class for Attacker
#     :params:
#         optim: name of attack algorithm
#         max_iter: maximum number of iterations
#         eps: epsilon param
#     """
#     def __init__(self, optim, max_iter=10, eps=8/255, eps1=8/255, eps2=8/255):
#         self.max_iter = max_iter
#         self.eps = eps
#         self.eps1 = eps1
#         self.eps2 = eps2
#         self.optim = optim

#     def _generate_tensors(self, query):
#         """
#         Generate tensors to allow computing gradients
#         :params:
#             query: list of cv2 image
#         :return: torch tensors of images
#         """
#         return generate_tensors(query)

#     def _generate_adv(self, images):
#         """
#         Generate adversarial image
#         :params:
#             images: list of cv2 image
#         :return: adversarial cv2 image
#         """
#         raise NotImplementedError("This is an interface method")

#     def _generate_targets(self, victim, images):
#         """
#         Generate target for image using victim model
#         :params:
#             images: list of cv2 image
#             victim: victim detection model
#         :return:
#             targets: targets for image
#         """
#         raise NotImplementedError("This is an interface method")

#     def _iterative_attack(self, att_img, targets, model, optim, max_iter, mask=None):
#         """
#         Performs iterative adversarial attack on image
#         :params:
#             att_img: input attack image
#             targets: attack targets
#             model: victim detection model
#             optim: optimizer
#             max_iter: number of attack iterations
#             mask: gradient mask
#         :return:
#             results: tensor image with updated gradients
#         """

#         for _ in range(max_iter):
#             optim.zero_grad()
#             with torch.set_grad_enabled(True):
#                 loss = model(att_img, targets)
#             loss.backward()

#             if mask is not None:
#                 att_img.grad[mask] = 0

#             optim.step()

#         results = att_img.clone()
#         return results

#     def attack(self, victim, query_images, targets=None, optim_params={}):
#         """
#         Performs attack flow on image
#         :params:
#             query_images: raw cv2 image
#             victim: victim detection model
#             targets: targets for image
#             optim_params: keyword arguments that will be passed to optim
#         :return:
#             adv_res: adversarial cv2 image
#         """
#         # Generate target
#         if targets is None:
#             targets = self._generate_targets(victim, query_images)

#         # Generate adverasarial
#         adv_imgs = self._generate_adv(query_images)
#         adv_norm = victim.preprocess(adv_imgs)

#         # To tensor, allow gradients to be saved
#         adv_tensors = self._generate_tensors(adv_norm)

#         # Get attack algorithm
#         optim = get_optim(self.optim, params=[adv_tensors], epsilon=self.eps, **optim_params)

#         # Adversarial attack
#         adv_tensors.requires_grad = True
#         adv_res = self._iterative_attack(adv_tensors, targets, victim, optim, self.max_iter)

#         # Postprocess, return cv2 image
#         adv_res = victim.postprocess(adv_res)
#         return adv_res

In [ ]:
# import torch

# class FullAttacker(Attacker):
#     """
#     Adversarial attack on Face Detection / Landmark Estimation / Gaze Estimation models
#     :params:
#         optim: name of attack algorithm
#         max_iter: maximum number of iterations
#         eps: epsilon param
#     """

#     def __init__(self, optim, max_iter=250, eps=8/255, eps1=8 / 255.0, eps2= 8/255):
#         super().__init__(optim, max_iter, eps, eps1, eps2)

#     def _generate_targets(self, victims, images):
#         """
#         Generate target for image using victim models
#         :params:
#             images: list of cv2 image
#             victims: dictionary of victim models.
#         :return:
#             targets_dict: dict of targets which required for _iterative_attack method
#         """

#         targets_dict = {}

#         # Generate detection targets
#         # Normalize image
#         det_query = victims["detection"].preprocess(images)

#         # To tensor, allow gradients to be saved
#         # det_query_tensor = self._generate_tensors(det_query)

#         # Detect on raw image
#         predictions = victims["detection"].detect(det_query)

#         # Make targets and face_box
#         det_targets = victims["detection"].make_targets(predictions, det_query)

#         # face_boxes = victims["detection"].get_face_boxes(predictions)
#         bboxes = victims["detection"].get_bboxes(predictions)

#         targets_dict["detection"] = det_targets

#         # Generate OCR targets
#         if "OCR" in victims.keys():
#             # Normalize image
#             rec_query = victims["OCR"].preprocess(det_query, bboxes)

#             # Detect on raw image
#             rec_predictions = victims["OCR"].detect(rec_query)

#             # Make targets
#             ocr_targets = victims["OCR"].make_targets(rec_predictions, rec_query)
#             targets_dict["OCR"] = ocr_targets

#         return targets_dict

#     def _iterative_attack(self, att_imgs, targets, victims, optim, max_iter, mask=None):
#         """
#         Performs iterative adversarial attack on batch images
#         :params:
#             att_imgs: input attack image
#             targets: dictionary of attack targets
#             victims: dictionary of victim models.
#             optim: optimizer
#             max_iter: maximum number of attack iterations
#             mask: gradient mask
#         :return:
#             results: tensor image with updated gradients
#         """

#         # Batch size for normalizing loss
#         batch_size = att_imgs.shape[0]

#         iter = 0
#         # Start attack
#         while True:
#             optim.zero_grad()
#             with torch.set_grad_enabled(True):

#                 # Forward face detection model
#                 det_loss = victims["detection"](att_imgs, targets["detection"])

#                 if "OCR" in victims.keys():
#                     # Generate cropped tensors to prepare for OCR model
#                     # Apply other kind of attack here
#                     #===== TODO (OR NOT) ===== #

#                     #===== ATTACK OCR ======= #
#                     # Forward ocr model
#                     ocr_loss = victims["OCR"](att_imgs, targets["OCR"])


#                 # Sum up loss
#                 if det_loss.item() / batch_size > self.eps1:
#                     loss = det_loss
#                 elif "OCR" in victims.keys() and ocr_loss.item() / batch_size > self.eps2:
#                     loss = ocr_loss + det_loss
#                 else:
#                     break

#                 loss.backward()


#             if mask is not None:
#                with torch.no_grad():
#                   att_imgs.grad *= mask

#             optim.step()

#             iter += 1
#             if iter == max_iter:
#                 break

#         print("Number of iter: ", iter)
#         return att_imgs

#     def attack(self, victims, images, deid_images, optim_params={}):
#         """
#         Performs attack flow on image
#         :params:
#             images: list of rgb cv2 images
#             victims: dictionary of victim models.
#             deid_images: list of De-identification cv2 images
#             optim_params: keyword arguments that will be passed to optim
#         :return:
#             adv_res: adversarial cv2 images
#         """

#         # assert (
#         #     "detection" in victims.keys() and "alignment" in victims.keys()
#         # ), "Need both detection and alignment models to attack"

#         targets = self._generate_targets(victims, images)

#         # Process deid images for detection model
#         deid_norm = victims["detection"].preprocess(deid_images)

#         # To tensors and turn on gradients flow
#         deid_tensor = self._generate_tensors(deid_norm)
#         deid_tensor.requires_grad = True

#         # Get attack algorithm
#         optim = get_optim(
#             self.optim, params=[deid_tensor], epsilon=self.eps, **optim_params
#         )

#         # Start iterative attack
#         adv_res = self._iterative_attack(
#             deid_tensor,
#             targets=targets,
#             victims=victims,
#             optim=optim,
#             max_iter=self.max_iter,
#         )

#         # Postprocess, return cv2 image
#         adv_images = victims["detection"].postprocess(adv_res)
#         return adv_images


In [ ]:
# def attack(batch, adv_images, attacker, victims):
#   adv_imgs = attacker.attack(
#       victims=victims,
#       images=batch,
#       deid_images=adv_images)
#   return adv_imgs

#### Online test

##### Detection

In [ ]:
# image_paths = [ "/content/LP_detection_11/images/train/xemay1030.jpg",  "/content/LP_detection_11/images/train/xemay1018.jpg"]
# images = [cv2.imread(path) for path in image_paths]
# bboxes = [get_bbox(path, image.shape[1], image.shape[0]) for path, image in zip(image_paths, images)]
# visualize_bbox(images[0], bboxes[0])

In [ ]:
# from _models.detection.YoLoDetect import YOLOv5Detector
# detect_model = YOLOv5Detector()

YOLOv5 🚀 2025-2-3 Python-3.11.11 torch-2.5.1+cu124 CPU

Fusing layers... 
Model summary: 290 layers, 20852934 parameters, 0 gradients, 47.9 GFLOPs
Adding AutoShape... 


In [ ]:
# images = detect_model.preprocess(images)
# print(images.shape)

(2, 640, 640, 3)


In [ ]:
# predictions = detect_model.detect(images)
# print(predictions)

/content/adversarial_pertubation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_pertubation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.



[[[196.08792114257812, 258.7448425292969, 310.4970397949219, 353.0282287597656, 0.9403959512710571, 0, 'license_plate']], [[264.0097351074219, 216.03427124023438, 388.0444030761719, 318.7881164550781, 0.9407525062561035, 0, 'license_plate']]]


In [ ]:
# targets = detect_model.make_targets(predictions, images)
# print(targets)

tensor([[0.00000, 0.00000, 0.39577, 0.47795, 0.17876, 0.14732],
        [1.00000, 0.00000, 0.50942, 0.41783, 0.19380, 0.16055]])


##### OCR

In [ ]:
# from _models.OCR.YoloOCR import YoloLicensePlateOCR
# ocr_model = YoloLicensePlateOCR()

YOLOv5 🚀 2025-2-3 Python-3.11.11 torch-2.5.1+cu124 CPU

Fusing layers... 
Model summary: 290 layers, 20970123 parameters, 0 gradients, 48.2 GFLOPs
Adding AutoShape... 


In [ ]:
# bboxes = detect_model.get_bboxes(predictions)
# crop_images = ocr_model.preprocess(images, bboxes)
# print(images.shape)

(2, 640, 640, 3)


In [ ]:
# predictions = ocr_model.detect(crop_images)
# print(predictions)

/content/adversarial_pertubation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.

/content/adversarial_pertubation/_models/detection/_models/yolov5/models/common.py:894: FutureWarning:

`torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.



[[[132.3191375732422, 112.39067840576172, 202.16236877441406, 290.7901611328125, 0.9004077911376953, 4, '5'], [231.01583862304688, 332.527099609375, 300.2917785644531, 503.94256591796875, 0.8811461329460144, 29, '0'], [442.56976318359375, 343.55706787109375, 508.627197265625, 513.6678466796875, 0.8781945109367371, 7, '8'], [449.89715576171875, 131.11309814453125, 513.9876708984375, 303.29571533203125, 0.877473771572113, 2, '3'], [128.31692504882812, 329.278076171875, 194.67074584960938, 497.89599609375, 0.8640832304954529, 29, '0'], [216.20571899414062, 126.58441925048828, 274.79742431640625, 293.9416198730469, 0.8585613965988159, 3, '4'], [338.84332275390625, 339.0281066894531, 389.6031494140625, 511.3060607910156, 0.8413061499595642, 0, '1']], [[399.1671142578125, 327.3040771484375, 463.85430908203125, 497.18634033203125, 0.8832429051399231, 2, '3'], [132.3690185546875, 133.21563720703125, 198.0614013671875, 307.2659606933594, 0.8818169832229614, 5, '6'], [359.2890319824219, 116.9191

In [ ]:
# targets = ocr_model.make_targets(predictions, images)
# print(targets)

tensor([[ 0.00000,  4.00000,  0.26131,  0.31499,  0.10913,  0.27875],
        [ 0.00000, 29.00000,  0.41508,  0.65349,  0.10824,  0.26784],
        [ 0.00000,  7.00000,  0.74312,  0.66971,  0.10321,  0.26580],
        [ 0.00000,  2.00000,  0.75304,  0.33938,  0.10014,  0.26904],
        [ 0.00000, 29.00000,  0.25233,  0.64623,  0.10368,  0.26347],
        [ 0.00000,  3.00000,  0.38360,  0.32854,  0.09155,  0.26150],
        [ 0.00000,  0.00000,  0.56910,  0.66432,  0.07931,  0.26918],
        [ 1.00000,  2.00000,  0.67424,  0.64413,  0.10107,  0.26544],
        [ 1.00000,  5.00000,  0.25815,  0.34413,  0.10264,  0.27195],
        [ 1.00000, 10.00000,  0.61282,  0.31893,  0.10287,  0.27249],
        [ 1.00000, 29.00000,  0.20209,  0.67379,  0.10647,  0.26298],
        [ 1.00000, 29.00000,  0.37535,  0.33087,  0.10176,  0.28024],
        [ 1.00000,  3.00000,  0.35071,  0.66810,  0.09704,  0.26553],
        [ 1.00000, 29.00000,  0.49433,  0.66208,  0.10694,  0.27630],
        [ 1.00000,  

In [ ]:
# lps, _ = ocr_model.get_plates_and_bboxes(predictions)
# for lp in lps:
#   print(lp)

543-0018
60B1-04034


In [ ]:
# visualize(images[0], bboxes[0], lps[0])

In [ ]:
# visualize(images[1], bboxes[1], lps[1])